In [14]:
import os, sumolib
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib_venn import venn2, venn3
from datetime import datetime

In [15]:
class DailyPreprocessor:
    def __init__(self, config_name='revised', nowTime=datetime.now()):
        self.config_name = config_name
        self.nowTime = nowTime
self = DailyPreprocessor(nowTime = datetime.now())

In [16]:
self.net = sumolib.net.readNet('new_sungnam_network_internal_target_0811.net.xml')

In [17]:
# ## 교차로목록 정의
# sixties = pd.read_excel('교차로기반정보_(시범지역).xlsx', header=1)
# self.inter_nos = set(sixties['교차로 ID'].dropna().astype(int))
# # 551, 561은 TC_IF_TOD_RED_YELLO, TN_IF_SIGL_FLOW에 존재하지 않음. TOD 보고서에서도 확인할 수 없음
# # 551 : 보육시설 삼거리, 561 : 공영주차장 단일로


# self.inter_nos = self.inter_nos - {551, 561}
# # 464는 매칭테이블에 존재하지 않음. 500에 매칭되는 node_id가 네트워크에 존재하지 않음.
# # 464 : 성남공판장 단일로, 500 : 단남아파트 단일로
# self.inter_nos = self.inter_nos - {464, 500}
# print(len(self.inter_nos))
# inter_nos_display = ", ".join(map(str, sorted(self.inter_nos)))
# inter_nos_display = "\n".join([inter_nos_display[i:i+100] for i in range(0, len(inter_nos_display), 100)])
# # print(len(inter_nos_display))
# print(inter_nos_display)

In [72]:
## 매칭테이블 정의, 교차로-노드 딕셔너리 정의
self.inter_node = pd.read_excel('signal_node_matching.xlsx', dtype={'node_id':str})
self.inter_node = self.inter_node.rename(columns={'signal_id':'inter_no'})
self.inter_node['inter_type'] = 'parent'
self.inter_node = self.inter_node[self.inter_node.node_id.isin(node.getID() for node in self.net.getNodes())]

In [18]:
## 매칭테이블 정의, 교차로-노드 딕셔너리 정의
self.inter_node = pd.read_excel('signal_node_matching.xlsx', dtype={'node_id':str})
self.inter_node = self.inter_node.rename(columns={'signal_id':'inter_no'})
self.inter_node['inter_type'] = 'parent'
# self.inter_node = self.inter_node[self.inter_node.inter_no.isin(self.inter_nos)].reset_index(drop=True)
self.inter_nos = sorted(self.inter_node.inter_no)

# 일대일대응 확인
if not len(self.inter_node) == self.inter_node.inter_no.nunique() == self.inter_node.node_id.nunique():
    raise ValueError("Warning: 'inter_no'와 'node_id' 간에 일대일대응 관계가 성립하지 않습니다.")

# 교차로번호 vs 노드id 간 딕셔너리
self.inter2node = dict(zip(self.inter_node.inter_no, self.inter_node.node_id))
self.node2inter = dict(zip(self.inter_node.node_id, self.inter_node.inter_no))
self.node_ids = {self.inter2node[inter_no] for inter_no in self.inter_nos}

In [19]:
# net = sumolib.net.readNet('new_sungnam_network_internal_0809.net.xml')
# inter_node = pd.read_excel('signal_node_matching.xlsx', dtype={'node_id':str})
# print(len(set(inter_node.signal_id)))
# print(inter_nos - set(inter_node.signal_id))
# inter_node = inter_node[inter_node.node_id.isin(node.getID() for node in net.getNodes())]
# print(len(set(inter_node.signal_id)))
# print(inter_nos - set(inter_node.signal_id))

In [20]:
## 테이블 표준화

# 주요 테이블 로드 (실제로는 쿼리문 작성 부분이 되어야 함.)
self.dayplan  = pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TC_IF_TOD_DAY_PLAN.csv'))
self.holyplan = pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TC_IF_TOD_HOLIDAY_PLAN.csv'))
self.red_yel  = pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TC_IF_TOD_RED_YELLO.csv'))
self.weekplan = pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TC_IF_TOD_WEEK_PLAN.csv'))
# 교차로정보 테이블은 불러오지 않음 (해당 테이블이 실질적으로 쓰이지는 않고, 60개 테이블 정보가 있지도 않음)
# inter_info=pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TM_FA_CRSRD.csv'))
self.flows    = pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TN_IF_SIGL_FLOW.csv'))

# 유효한 교차로들에 대하여만 슬라이싱
self.dayplan = self.dayplan[self.dayplan.CRSRD_ID.isin(self.inter_nos)]
self.weekplan= self.weekplan[self.weekplan.CRSRD_ID.isin(self.inter_nos)]
self.red_yel = self.red_yel[self.red_yel.CRSRD_ID.isin(self.inter_nos)]
self.flows   = self.flows[self.flows.CRSRD_ID.isin(self.inter_nos)]

# 컬럼명 변경 적용
rename_cname_1 = {'CRSRD_ID':'inter_no',        'CYCL':'cycle',             'DAY':'DD',
                  'HOUR':'hh',                  'MIN':'mm',                 'MNTH':'MM',
                  'OFFSET':'offset',            'PHASE':'phase_no',         'PLAN_NO':'plan_no',
                  'RINGA_RED_SEC':'red_A',      'RINGA_YELLO_SEC':'yel_A',  'RINGB_RED_SEC':'red_B',
                  'RINGB_YELLO_SEC':'yel_B'}

rename_cname_2 = {f'RING{alph}_PHASE{i}':f'dura_{alph}{i}' for alph in ['A', 'B'] for i in range(1,9)}
rename_cname = {**rename_cname_1, **rename_cname_2}
self.dayplan  = self.dayplan.rename(columns=rename_cname)
self.holyplan = self.holyplan.rename(columns=rename_cname)
self.weekplan = self.weekplan.rename(columns=rename_cname)
self.red_yel  = self.red_yel.rename(columns=rename_cname)

In [21]:
## self.plan : 신호계획 테이블 생성

# 날짜, 요일 지정
MM, DD = self.nowTime.month, self.nowTime.day # 날짜
dow_number = self.nowTime.weekday() # 요일
hplan = self.holyplan[(self.holyplan.MM==MM) & (self.holyplan.DD==DD)]
dows = [dow for dow in self.weekplan.columns if dow.endswith('PLAN_NO')]
dows = dows[1:] + dows[0:1]
dow = dows[dow_number]

# (신호교차로, 신호계획번호) 목록
if len(hplan):
    inter_pnos = list(zip(hplan['inter_no'], hplan['plan_no']))
else:
    inter_pnos = list(zip(self.weekplan.inter_no, self.weekplan[dow]))

# 신호테이블 통합
self.plan = self.dayplan.copy()
self.plan['inter_pno'] = list(zip(self.plan['inter_no'], self.plan['plan_no']))
self.plan = self.plan[(self.plan.inter_pno.isin(inter_pnos))]
self.plan = self.plan.drop(columns='inter_pno')
max_phase_no = int(self.red_yel.phase_no.max())
for j in range(1,max_phase_no+1):
    RY = self.red_yel[self.red_yel.phase_no==j].iloc[0]
    red_A = RY.red_A
    red_B = RY.red_B
    yel_A = RY.yel_A
    yel_B = RY.yel_B
    self.plan[f'red_A{j}'] = red_A
    self.plan[f'red_B{j}'] = red_B
    self.plan[f'yellow_A{j}'] = yel_A
    self.plan[f'yellow_B{j}'] = yel_B

In [22]:
## self.angle : 각도(이동류방향) 테이블 생성
self.angle = self.flows.copy()
self.angle = self.angle.rename(columns={'CRSRD_ID':'inter_no',    'PHASE':'phase_no',
                              'RING':'ring_type',       'FLOW_NO':'move_no'})
# 유효한 이동류번호 및 교차로번호로 슬라이싱
self.angle = self.angle[self.angle.move_no.isin(range(1,19))]
self.angle = self.angle[self.angle.inter_no.isin(self.inter_nos)]
# 세 점 데이터 파싱 및 각도코드 열 생성
for ind, row in self.angle.iterrows():
    arrow = row.SIGL_ARROW
    # 위경도 추출
    # arrow = re.findall(r'-?\d+\.?\d*', arrow)
    arrow = [coord.lstrip(' ') for coord in arrow.split(',')]
    arrow = [coord.lstrip('[') for coord in arrow]
    arrow = [coord.rstrip(']') for coord in arrow]
    exists = all([bool(coord) for coord in arrow])
    if exists:
        y1, x1, y2, x2, y3, x3 = arrow

        # 미터 단위로 변환
        x1, y1 = self.net.convertLonLat2XY(x1, y1)
        x2, y2 = self.net.convertLonLat2XY(x2, y2)
        x3, y3 = self.net.convertLonLat2XY(x3, y3)

        # 진입각, 진출각 설정
        inc_angle = np.arctan2(y1 - y2, x1 - x2)
        out_angle = np.arctan2(y3 - y2, x3 - x2)
        inc_angle = inc_angle * 180 / np.pi
        out_angle = out_angle * 180 / np.pi
        inc_angle = int((90 - inc_angle) % 360)
        out_angle = int((90 - out_angle) % 360)

        # 각도코드 설정
        angle_code = str(inc_angle).zfill(3) + str(out_angle).zfill(3)
        self.angle.loc[ind, 'angle_code'] = angle_code
    else:
        self.angle.loc[ind, 'angle_code'] = None
self.angle = self.angle.drop(columns='SIGL_ARROW')
self.angle = self.angle.reset_index(drop=True)\
    .sort_values(by=['inter_no', 'phase_no', 'ring_type']).reset_index(drop=True)
self.angle

inter_no  phase_no ring_type  move_no  STOS_NO angle_code
0         436         1         A        5        0     262358
1         436         1         B        2        0     262074
2         436         2         A        8        0     174355
3         436         2         B        3        0     172263
4         436         3         A        7        0     356074
..        ...       ...       ...      ...      ...        ...
354       639         4         A        6        0     120312
355       639         4         B        1        0     126221
356       640         1         A        8        0     226052
357       640         1         B        4        0     043222
358       640         2         A       17        0       None

[359 rows x 6 columns]

In [23]:
## self.match1 테이블 생성
match1 = self.flows.copy()
match1 = match1[['CRSRD_ID', 'PHASE', 'RING', 'FLOW_NO']]
match1 = match1.rename(columns={'CRSRD_ID':'inter_no',  'PHASE':'phase_no', 'RING':'ring_type', 'FLOW_NO':'move_no'})
match1 = match1.sort_values(by=['inter_no', 'phase_no', 'ring_type']).reset_index(drop=True)
# 유효한 이동류번호 및 교차로번호로 슬라이싱
match1 = match1[match1.move_no.isin(range(1,19))]
match1 = match1[match1.inter_no.isin(self.inter_nos)]
# 특정한 (교차로번호, 현시번호)에 대하여 한 링에 대해서만 이동류번호만 정의된 경우, 나머지 링에 대해서 이동류 정의
additional_m1s = []
for key, group in match1.groupby(['inter_no', 'phase_no']):
    inter_no, phase_no = map(int,key)
    if set(group.ring_type) != {'A', 'B'}:
        assert len(group)==1
        ring_type = group.iloc[0].ring_type
        RING_TYPE = list({'A', 'B'} - set(ring_type))[0]
        additional_m1 = group.copy()
        additional_m1['ring_type'] = RING_TYPE
        additional_m1s.append(additional_m1)
match1 = pd.concat([match1] + additional_m1s)
match1 = match1.reset_index(drop=True)
display(match1)
# 열 재편 : 현시시간과 이동류번호 열을 A, B로 구분
match1s = []
for key, group in match1.copy().groupby(['inter_no', 'phase_no']):
    inter_no, phase_no = map(int, key)
    assert len(group) == 2
    row_A = group[group.ring_type=='A']
    row_B = group[group.ring_type=='B']
    assert len(row_A)==len(row_B)==1
    row_A = row_A.iloc[0]
    row_B = row_B.iloc[0]
    m1 = pd.DataFrame({'inter_no':[inter_no], 'phas_A':[phase_no], 'phas_B':[phase_no],
                       'move_A':[row_A.move_no], 'move_B':[row_B.move_no]})
    match1s.append(m1)
display(match1)
self.match1 = pd.concat(match1s).reset_index(drop=True)

inter_no  phase_no ring_type  move_no
0         436         1         A        5
1         436         1         B        2
2         436         2         A        8
3         436         2         B        3
4         436         3         A        7
..        ...       ...       ...      ...
367       576         2         B       17
368       582         2         B       17
369       632         2         B       17
370       634         4         B        5
371       640         2         B       17

[372 rows x 4 columns]

inter_no  phase_no ring_type  move_no
0         436         1         A        5
1         436         1         B        2
2         436         2         A        8
3         436         2         B        3
4         436         3         A        7
..        ...       ...       ...      ...
367       576         2         B       17
368       582         2         B       17
369       632         2         B       17
370       634         4         B        5
371       640         2         B       17

[372 rows x 4 columns]

In [73]:
os.listdir()

['make_intermediates.ipynb',
 'new_sungnam_network_internal_0809.net.xml',
 'new_sungnam_network_internal_0811.net.xml',
 'new_sungnam_network_internal_target_0811.net.xml',
 'nodes.json',
 'signal_node_matching.xlsx',
 'signal_node_matching_0809.xlsx',
 'sn_admin_tables',
 'turn_type_info.csv',
 'uturn_data_info.csv',
 '교차로기반정보_(시범지역).xlsx']

In [78]:
self.uturn = pd.read_csv('uturn_data_info.csv')
self.u_condition = self.uturn.copy()[['child_id']]
self.u_condition['condition'] = '좌회전시'
self.u_condition

child_id condition
0     109187      좌회전시
1     109188      좌회전시
2     109189      좌회전시
3     109192      좌회전시
4     109193      좌회전시
5     109595      좌회전시
6     107169      좌회전시
7     108093      좌회전시
8     108098      좌회전시
9     108102      좌회전시
10    108099      좌회전시
11    108106      좌회전시
12    107717      좌회전시
13    110754      좌회전시
14    109205      좌회전시
15    107270      좌회전시

In [24]:
# # self.coord : 연등교차로 테이블 생성
# self.coord = pd.DataFrame(columns=['parent_id', 'child_id', 'phase_no', 'ring_type', 'inc_edge_id', 'out_edge_id'])

In [27]:
# dfs = {'dayplan':dayplan, 'red_yel':red_yel, 'weekplan':weekplan, 'flows':flows}
# for df_name, df in dfs.items():
#     print(df_name)
#     assert set(df.CRSRD_ID).issubset(inter_nos)
#     inter_no_coincide = inter_nos == set(df.CRSRD_ID)
#     if not inter_no_coincide:
#         print(f"  inter_no's doesn't conicide.")
#         print(f"  missing inter_no's : {inter_nos - set(df.CRSRD_ID)}")

In [ ]:
# venn3([set(dayplan.CRSRD_ID), set(red_yel.CRSRD_ID), set(weekplan.CRSRD_ID)], ('dayplan', 'redyel', 'weekplan'))
# plt.show()
# print(f'일간계획 테이블의 교차로 개수 : {len(set(dayplan.CRSRD_ID))}')
# print(f'황색적색 테이블의 교차로 개수 : {len(set(red_yel.CRSRD_ID))}')
# print(f'주간계획 테이블의 교차로 개수 : {len(set(weekplan.CRSRD_ID))}')
# CRSRD_IDs_plan = set(dayplan.CRSRD_ID) & set(red_yel.CRSRD_ID) & set(weekplan.CRSRD_ID)
# print(f'겹치는 교차로 개수 : {len(CRSRD_IDs_plan)}')
# print(f'겹치는 교차로 목록 : {sorted(CRSRD_IDs_plan)}')